# Applications of Data Analysis
## Exercise 4
### Tiina Nokelainen 503737

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import math
from sklearn.neighbors import KNeighborsRegressor

inputs = pd.read_csv("input.csv", header=None)
outputs = pd.read_csv("output.csv", header=None)
coordinates = pd.read_csv("coordinates.csv", header=None)

In [2]:
# z-score to input datas
zscore = lambda x: (x - x.mean()) / x.std()
inputs = inputs.transform(zscore)

# combine all three datasets into one dataset
# first column has real values, second and third has coordinates, the rest are features
dataset = pd.concat([outputs, coordinates, inputs], axis=1, ignore_index=True).values

In [3]:
def distance(x, y):
    
    dis = math.pow((y[1] - x[1]),2) + math.pow((y[2] - x[2]),2)
    return math.sqrt(dis)

In [4]:
# SLOO 
# inputs: dataset, dead zone radius: d, number of neighbors: k
# returns: C-index with given values of d and k
def sloo(dataset, d, k):
    
    # list of predicted values 
    predictions = []
    # list of true values
    truevalues = []
    
    for i in range(len(dataset)):
        
        # trainset with samples outside of the dead zone (distance is bigger than d)
        trainset = np.array(list(filter(lambda x: distance(x, dataset[i]) > d, dataset)))
        
        # splits the data into trainset's features X_train and values Y_train
        X_train, Y_train = trainset[:,3:], trainset[:,0]
        # test sample's features: X_test
        # test sample's real value: Y_test
        X_test, Y_test = dataset[i,3:], dataset[i,0]
        
        print(X_train)
        print(Y_train)
        print(X_test)
        knr = KNeighborsRegressor(n_neighbors=k)
        knr.fit(X_train, Y_train)
        
        # saves predictions and realvalues into separates lists
        predictions += list(knr.predict([X_test]))
        truevalues += [Y_test]
        
    return cindex(predictions, truevalues)

In [5]:
# code from the slides
# inputs: list of predicted velus: predictions, list of real values: truevalues
# returns: C-index
def cindex(predictions, truevalues):
    n = 0
    n_sum = 0
    for i in range(len(truevalues)):
        t = truevalues[i]
        p = predictions[i]
        for j in range(i+1,len(truevalues)):
            nt = truevalues[j]
            np = predictions[j]
            if (t != nt):
                n += 1
                if (p < np and t < nt) or (p > np and t > nt):
                        n_sum += 1
                elif p == np:
                    n_sum += 0.5
    return n_sum/n

In [ ]:
k_values = [1,3,5,7,9]
cindexs = []

# SLOO for every value of d and k
for d in range(0, 210, 10):
    d_cindex = {}
    
    for k in k_values:
        d_cindex[str(k)] = sloo(dataset, d, k)
    
    # save the best value of c-index and k
    best_k = max(d_cindex, key=d_cindex.get)
    max_c = d_cindex.get(best_k)
    
    cindexs.append({'d' : d, 'k' : best_k, 'C-index' : round(max_c, 4)})

[[-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 [-0.27256    -0.50770845 -0.47469094 ...  0.46710009  0.10741776
  -0.83268687]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[6.2592 6.9041 6.2065 ... 4.6098 5.853  4.1202]
[-0.27256     0.24740523  0.18671619  0.17578758  0.23122223 -0.48605579
  0.27743347  0.25518456  0.66267111  0.2255628   0.41216997  0.51364828
  0.2853881   0.08331717  0.43975021 -0.05537776 -0.17295481 -0.14223016
 -0.14994733 -0.58057532 -0.05318054 -0.21923119  0.20995826  0.70421657
  0.33937639  0.41251621  0.33097647 -0.03440105 -0.18442595  0.30725441
  0.40316672  0.23497052 -0.95366075 -0.27298504 -0.06438079 -0.53752868
 -0.18970253 -0.096945

[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256    -0.43161172 -0.45010331 -0.48405995 -0.35517967 -0.04437092
 -0.33357176 -0.41115602 -1.0908281  -0.9568695  -0.96236911 -1.02517321
 -1.07086517 -1.06669553 -1.00940527 -0.84647714 -0.82741248 -0.85067614
 -0.86306517 -0.83723758 -0.85697291 -0.83258801 -1.59469719 -1.74983849
 -1.96922102 -1.0150585  -0.76367804 -0.03440105 -0.29363852 -0.29347849
 -0.79589973 -1.47487335 -1.14466398 -0.38604548 -0.82040796 -0.53752868
 -0.18970253 -0.096945

  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256    -0.57502479 -0.64680432 -0.62868407 -0.67503524 -0.52286287
 -0.58306556 -0.66948371 -0.84551992 -0.82017213 -0.75090156 -0.85419304
 -0.60110147 -0.96447218 -0.90262539 -0.44471463 -0.55718479 -0.51509646
 -0.41142387  0.6435062  -0.18178732 -0.54724905 -0.81621837 -0.98294628
 -1.09354614 -0.88527898 -0.92005726 -0.03440105 -0.33264301 -0.69396709
 -0.45330931 -0.98634653 -0.76265751 -0.337591   -0.58778422 -0.53752868
 -0.18970253 -0.09694581 -1.18168548 -1.10371668  0.38808903  0.36520774
 -0.3991442  -0.54343293 -0.77802746 -0.33940123 -0.33093088 -0.38670704
 -0.41500043  1.96996561  0.11306429 -0.49987786 -0.45020598 -0.52068289
 -0.60923456 -0.53589339 -0.40403596 -0.48736597  5.20089478  1.42301375
 -1.0045698  -0.93211777 -0.48454082 -0.39877656 -0.43389308 -0.72028363
 -0.75637002  1.46915098  0.71586665  0.27662077 -0.58635763 -0.42230493
 -0.41941544 -0.75850173  1.50967243  1.01402804 -1.13642253

  0.45733666  0.5799317   0.81575443 -0.33904539 -0.29627391]
[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256     0.18301569  0.16458733  0.17578758  0.17791297 -0.41244165
  0.11959045  0.21414184  0.86255185 -0.14352012  0.14783553  0.34266811
 -0.29045128  0.54332225  0.18551241 -0.84647714 -0.82741248 -0.85067614
 -0.86306517 -0.83723758 -0.85697291 -0.83258801  0.42227067  0.0907028
 -0.19133566  0.15295718  0.33097647 -0.03440105 -0.19222685  0.24050631
  0.40316672 -0.9049254  -0.380651

  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256     0.18886929  0.16950485  0.17578758  0.17791297 -0.39403811
  0.11959045  0.22138467  0.88980832 -0.12985038  0.16545783  0.34266811
 -0.26772077  0.56887809  0.20076668 -0.84647714 -0.82741248 -0.85067614
 -0.86306517 -0.83723758 -0.85697291 -0.83258801  0.42227067  0.0907028
 -0.19133566  0.15295718  0.33097647 -0.03440105 -0.19222685  0.24050631
  0.40316672 -0.9049254  -0.38065104 -0.38604548 -0.82040796 -0.53752868
 -0.18970253 -0.09694581 -0.31260637 -0.39364035  0.21094544  0.16929065
 -0.3991442  -0.62425648 -0.81984688  1.47109555 -0.33093088 -0.38670704
  3.53860934 -1.02497422  0.97343918 -0.49987786 -0.45020598 -0.52068289
 -0.60923456  0.78119728 -0.40403596 -0.48736597  0.63208345  0.81210346
 -0.16032583 -0.93211777 -0.48454082  1.133788   -0.43389308 -1.21860285
 -1.18501754 -0.04416738 -0.00431434 -0.19939574 -0.58635763 -0.42230493
 -0.41941544 -0.75850173 -0.37856909  1.01402804 -0.5572746  

...

[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-2.72559997e-01 -5.72097991e-01 -5.58288865e-01 -5.83489029e-01
 -4.88452823e-01 -3.20423965e-01 -4.91414775e-01 -5.34284171e-01
 -3.82160025e-01 -1.02510906e-01 -3.10344158e-01 -3.41252548e-01
 -7.07230910e-02  1.85540521e-01 -2.26352833e-01  1.86231338e+00
  1.43574437e+00  1.59781260e+00  1.63284728e+00  3.27614196e-01
  1.92950731e+00  1.34159731e+00 -9.75452674e-01 -6.26756374e-02
  4.74847621e-02 -2.36381385e-01 -2.94540394e-01 -3.44010518e-02
 -3.1

 -1.50563147e+00 -7.83412476e-01  1.26989008e+00]
[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256    -0.29405225 -0.25094355 -0.35751385 -0.19525188  1.44631555
 -0.01279401 -0.3544205   0.38102098  0.37592991  0.23594701  0.51364828
  0.55815413  0.72221311  0.63297094  1.63865178  1.45685591  1.5978126
  1.56153549  0.38684395  1.62942483  1.3025766  -0.99314537  0.0907028
  0.15362717  0.67207525  0.48735569 -0.03440105 -0.28583763 -0.42697469
 -0.62460452  1.61912985  0.38336191 -0.0064854

[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-2.72559997e-01 -5.72097991e-01 -5.58288865e-01 -5.83489029e-01
 -4.88452823e-01 -3.20423965e-01 -4.91414775e-01 -5.34284171e-01
 -3.82160025e-01 -1.02510906e-01 -3.10344158e-01 -3.41252548e-01
 -7.07230910e-02  1.85540521e-01 -2.26352833e-01  1.86231338e+00
  1.43574437e+00  1.59781260e+00  1.63284728e+00  3.27614196e-01
  1.92950731e+00  1.34159731e+00 -9.75452674e-01 -6.26756374e-02
  4.74847621e-02 -2.36381385e-01 -2.94540394e-01 -3.44010518e-02
 -3.1

[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256    -0.48722087 -0.4771497  -0.47502094 -0.43514356 -0.35723104
 -0.46086451 -0.4292631  -0.18227929 -0.10934577 -0.23985497 -0.17027238
  0.33084911  0.2366522  -0.12974247  1.43155771  1.03462515  1.17523079
  1.20497657  0.11043844  1.47938358  0.90871128 -0.72775487  0.0907028
  0.15362717 -0.10660186 -0.29454039 -0.03440105 -0.29363852 -0.29347849
 -0.62460452  1.13060302  0.95637161 -0.0710914   1.38951763 -0.53752868
 -0.18970253 -0.0969458

[[-0.27256     0.24740523  0.18671619 ... -0.10916092 -0.91336889
  -0.46134274]
 [-0.27256    -0.15063919 -0.14029923 ... -1.48153987 -1.08734279
  -0.46134274]
 [ 3.66674731 -0.57795159 -0.5951703  ...  0.34984306  0.13466668
  -0.80907569]
 ...
 [-0.27256     0.10691897  0.13016465 ...  2.18350037  3.52610979
   2.25824192]
 [-0.27256    -1.11062868 -1.1336393  ...  1.28865741  4.41065181
  11.25504219]
 [-0.27256    -1.11062868 -1.1336393  ...  0.51519906  5.56349093
  12.95089175]]
[5.8359 6.2592 6.9041 ... 4.6098 5.853  4.1202]
[-0.27256    -0.29112546 -0.24848478 -0.34847484 -0.16859724  1.44631555
 -0.01279401 -0.35200622  0.39010647  0.38959965  0.25356931  0.51364828
  0.56573096  0.74776895  0.64314046  1.64279366  1.46107821  1.5978126
  1.58530609  0.38684395  1.62942483  1.30501539 -0.99314537  0.0907028
  0.15362717  0.67207525  0.64373491 -0.03440105 -0.28583763 -0.42697469
 -0.62460452  1.61912985  0.38336191 -0.00648543  1.68029731  0.05968617
 -0.18970253 -0.09694581

In [ ]:
cindex_values = []
d_values = []
for i in range(21):
    cindex_values.append(cindexs[i].get('C-index'))
    d_values.append(cindexs[i].get('d'))
    
plt.plot(d_values, cindex_values, 'ro', color='blue', ms=5)
plt.xlabel('Dead zone radius', fontsize=14)
plt.ylabel('C-index value', fontsize=14)
plt.grid(True)
plt.show()

In [ ]:
sloo(dataset,0,0)

## Best C-index values for each dead zone radius

| Dead zone radius | Value of k | C-index value |
| --- | --- | --- |
| 0 | 9 | 0.7213 |
| 10 | 9 | 0.712 |
| 20 | 9 | 0.7112 |
| 30 | 9 | 0.7052 |
| 40 | 9 | 0.7041 |
| 50 | 9 | 0.7009 |
| 60 | 9 | 0.6992 |
| 70 | 9 | 0.6945 |
| 80 | 9 | 0.6908 |
| 90 | 7 | 0.6893 |
| 100 | 7 | 0.6875 |
| 110 | 7 | 0.6558 |
| 120 | 7 | 0.6346 |
| 130 | 7 | 0.6214 |
| 140 | 7 | 0.6192 |
| 150 | 7 | 0.6164 |
| 160 | 7 | 0.6175 |
| 170 | 7 | 0.6171 |
| 180 | 7 | 0.6161 |
| 190 | 7 | 0.6158 |
| 200 | 7 | 0.6147 |